# Analyse de l'incidence de la varicelle

In [1]:
 %matplotlib inline
import matplotlib.pyplot as plt
import pandas as pd
import isoweek

 Les données de l'incidence de la varicelle sont disponibles du site Web du Réseau Sentinelles. Nous les récupérons sous forme d'un fichier en format CSV dont chaque ligne correspond à une semaine de la période demandée. Nous téléchargeons toujours le jeu de données complet, qui commence en 1984 et se termine avec une semaine récente.

In [2]:
data_url = "http://www.sentiweb.fr/datasets/incidence-PAY-7.csv"
raw_data = pd.read_csv(data_url, skiprows=1)

In [3]:
raw_data[raw_data.isnull().any(axis=1)]

Empty DataFrame
Columns: [week, indicator, inc, inc_low, inc_up, inc100, inc100_low, inc100_up, geo_insee, geo_name]
Index: []

In [4]:
data = raw_data.dropna().copy()
data

week  indicator    inc  inc_low  inc_up  inc100  inc100_low  \
0     202422          7  11317     7330   15304      17          11   
1     202421          7   9807     6926   12688      15          11   
2     202420          7  13661    10209   17113      20          15   
3     202419          7  10083     6413   13753      15           9   
4     202418          7  13438     9514   17362      20          14   
5     202417          7  15303    11219   19387      23          17   
6     202416          7  18138    13540   22736      27          20   
7     202415          7  24929    17315   32543      37          26   
8     202414          7  16181    12544   19818      24          19   
9     202413          7  18322    14206   22438      27          21   
10    202412          7  12818     9128   16508      19          13   
11    202411          7  15973    12400   19546      24          19   
12    202410          7  14301    10761   17841      21          16   
13    202409          7  14337    10871   17803      21          16   
14    202408          7  15899    11991   19807      24          18   
15    202407          7  11294     8226   14362      17          12   
16    202406          7  12174     9020   15328      18          13   
17    202405          7   8814     6110   11518      13           9   
18    202404          7   9504     6566   12442      14          10   
19    202403          7   6948     4633    9263      10           7   
20    202402          7   7125     4852    9398      11           8   
21    202401          7  13305     9214   17396      20          14   
22    202352          7  11636     7354   15918      18          12   
23    202351          7   6912     4227    9597      10           6   
24    202350          7   8799     6215   11383      13           9   
25    202349          7   7817     5362   10272      12           8   
26    202348          7   7351     4749    9953      11           7   
27    202347          7   6537     4277    8797      10           7   
28    202346          7   5229     2973    7485       8           5   
29    202345          7   5007     2675    7339       8           4   
...      ...        ...    ...      ...     ...     ...         ...   
1718  199126          7  17608    11304   23912      31          20   
1719  199125          7  16169    10700   21638      28          18   
1720  199124          7  16171    10071   22271      28          17   
1721  199123          7  11947     7671   16223      21          13   
1722  199122          7  15452     9953   20951      27          17   
1723  199121          7  14903     8975   20831      26          16   
1724  199120          7  19053    12742   25364      34          23   
1725  199119          7  16739    11246   22232      29          19   
1726  199118          7  21385    13882   28888      38          25   
1727  199117          7  13462     8877   18047      24          16   
1728  199116          7  14857    10068   19646      26          18   
1729  199115          7  13975     9781   18169      25          18   
1730  199114          7  12265     7684   16846      22          14   
1731  199113          7   9567     6041   13093      17          11   
1732  199112          7  10864     7331   14397      19          13   
1733  199111          7  15574    11184   19964      27          19   
1734  199110          7  16643    11372   21914      29          20   
1735  199109          7  13741     8780   18702      24          15   
1736  199108          7  13289     8813   17765      23          15   
1737  199107          7  12337     8077   16597      22          15   
1738  199106          7  10877     7013   14741      19          12   
1739  199105          7  10442     6544   14340      18          11   
1740  199104          7   7913     4563   11263      14           8   
1741  199103          7  15387    10484   20290      27          18   
1742  199102          7  16277  

In [5]:
def convert_week(year_and_week_int):
    year_and_week_str = str(year_and_week_int)
    year = int(year_and_week_str[:4])
    week = int(year_and_week_str[4:])
    w = isoweek.Week(year, week)
    return pd.Period(w.day(0), 'W')

In [6]:
data['period'] = [convert_week(yw) for yw in data['week']]

In [7]:
sorted_data = data.set_index('period').sort_index()

In [ ]:
periods = sorted_data.index
for p1, p2 in zip(periods[:-1], periods[1:]):
    delta = p2.to_timestamp() - p1.end_time
    if delta > pd.Timedelta('1s'):
        print(p1, p2)

In [ ]:
sorted_data['inc'].plot()

In [ ]:
sorted_data['inc'][-200:].plot()

In [ ]:
first_september_week = [pd.Period(pd.Timestamp(y, 9, 1), 'W') for y in range(1985, sorted_data.index[-1].year)]

In [ ]:
year = []
yearly_incidence = []
for week1, week2 in zip(first_september_week[:-1], first_september_week[1:]):
    one_year = sorted_data['inc'][(sorted_data.index >= week1.start_time) & (sorted_data.index < week2.start_time)]
    assert abs(len(one_year)-52) < 2
    yearly_incidence.append(one_year.sum())
    year.append(week2.year)

In [ ]:
yearly_incidence.plot(style='*')

In [ ]:
yearly_incidence.sort_values()

In [ ]:
yearly_incidence.hist(xrot=20)